----
# <center>Dataset creation

In [15]:
import os
from pathlib import Path
import matlab.engine
import numpy as np
import shutil
import tempfile
import json

base_dir = Path("./")

 # --- Start MATLAB Engine ---
eng = matlab.engine.start_matlab()

 # --- Add SCOPE path to MATLAB's search path ---
scope_path = './SCOPE'  # e.g., '/home/user/Documents/SCOPE'
eng.addpath(scope_path, nargout=0)

# MODTRAN paths
modtran_dir = base_dir / "MODTRAN5"
modtran_exe = modtran_dir / "bin" / "Mod5_mac.exe" 
modtran_tp5_template = modtran_dir / "HyPlant-FLUO_Modtran5_base_v1.tp5"

# SCOPE paths
scope_dir = base_dir / "SCOPE"
scope_main = scope_dir / "SCOPE.m"
scope_wrapper = scope_dir / "run_scope_wrapper.m"

# Output directory
output_dir = base_dir / "synthetic_dataset"
output_dir.mkdir(exist_ok=True)

print(f"Checking path: {scope_dir.resolve()}")
print(f"Directory exists: {scope_dir.exists()}")
print(f"Directory contents: {list(scope_dir.glob('*')) if scope_dir.exists() else 'N/A'}")


Checking path: /home/omirako/Documents/MSc_Sensors_Imaging/Final_Project/SCOPE
Directory exists: True
Directory contents: [PosixPath('SCOPE/soltir_tp7.m'), PosixPath('SCOPE/bug_reports.txt'), PosixPath('SCOPE/README.md'), PosixPath('SCOPE/output'), PosixPath('SCOPE/SCOPE.m'), PosixPath('SCOPE/set_parameter_filenames.csv'), PosixPath('SCOPE/input'), PosixPath('SCOPE/run_scope_wrapper_json.m'), PosixPath('SCOPE/.readthedocs.yaml'), PosixPath('SCOPE/src'), PosixPath('SCOPE/GNU_General_Public_Licence.txt'), PosixPath('SCOPE/SCOPE.exe'), PosixPath('SCOPE/docs')]


In [16]:
from scopeWrapper import SCOPEWrapperMultiRun
import pandas as pd

if __name__ == "__main__":
    print("\n=== Path Diagnostics ===")
    print(f"Current working directory: {Path.cwd()}")
    print(f"Checking for 'SCOPE' in: {Path.cwd()}")

    # the spectral and scalar files that will be saved in the results.json
    
    spectral_files = {
        #"Eout_spectrum": "Eout_spectrum.csv",
        "Esun": "Esun.csv",
        #"Lo_spectrum": "Lo_spectrum.csv", 
        "fluorescence": "fluorescence.csv",
        #"sigmaF": "sigmaF.csv",
        "reflectance": "reflectance.csv",
    }
    
    scalar_files = {
        #"aPAR": "aPAR.csv",
        #"Eout": "Eout.csv",
        #"Lo": "Lo.csv",
        #"Esun": "Esun.csv",
        #"Esky": "Esky.csv",
        #"fluxes": "fluxes.csv",
        #"rad": "radiation.csv",
        #"fluorescence_scalars": "fluorescence_scalars.csv",
    }

    try:
        with SCOPEWrapperMultiRun(scalar_files=scalar_files, spectral_files=spectral_files) as scope:
            print("\n=== Running Multi-Simulation Test ===")
            # Example parameters (can be adjusted)

            # Run a simulation with multiple LAI and Cab values
            multi_params = {
                # PROSPECT leaf optical properties
                "Cab": [20.0, 25,0, 30.0, 40.0, 50.0],      # Chlorophyll content (μg/cm²)
                "Cca": [10.0],                  # Carotenoid content (μg/cm²)
                "Cdm": [0.012],                 # Dry matter content (g/cm²)
                "Cw": [0.009],                  # Equivalent water thickness (cm)
                "Cs": [0.0],                    # Senescent material fraction (0-1)
                "Cant": [1.0],                  # Anthocyanin content (μg/cm²)
                "N": [1.5],                     # Leaf structure parameter (-)

                # Leaf biochemical parameters
                "Vcmax25": [60.0],              # Maximum carboxylation rate at 25°C (μmol/m²/s)
                "BallBerrySlope": [8.0],        # Ball-Berry stomatal conductance slope
                "BallBerry0": [0.01],           # Ball-Berry intercept (mol/m²/s)

                # Canopy structure
                "LAI": [2.0, 3.0, 5.0, 8.00, 0.00],        # Leaf Area Index (m²/m²)
                "hc": [2.0],                    # Canopy height (m)
                "LIDFa": [-0.35],               # Leaf angle distribution parameter a (-)
                "LIDFb": [-0.15],               # Leaf angle distribution parameter b (-) this one has to vary

                # Soil parameters
                "rss": [500.0],                 # Soil respiration rate (μmol/m²/s)
                "SMC": [25.0],                  # Soil moisture content (%)
                
                # Meteorology
                "Rin": [800.0],                 # Incoming shortwave radiation (W/m²)
                "Ta": [20.0, 30.00],                   # Air temperature (°C)
                "Ca": [410.0],                  # Atmospheric CO₂ concentration (ppm)

                # Fluorescence
                "fqe": [0.01, 0.03, 0.06, 0.1, 0.2, 0.5, 1, 2], # Fluorescence quantum efficiency (-)

                # Angles
                "tts": [35.0, 0.00, 60.0],                  # Solar zenith angle (degrees)
                "tto": [0.0],                   # Observer zenith angle (degrees) +- 20 degrees
                "psi": [0.0]                    # Relative azimuth angle (degrees)
            }

            my_setoptions = {
                "simulation": 2,  # Enable Lookup-Table mode
                "calc_fluor": 1,  # Calculate fluorescence
                "soil_heat_method": 2,  # Use soil net radiation fraction
                "saveCSV": 1,  # Output CSV files
                "calc_planck": 0,
                "calc_directional": 0,
                "calc_planck": 0,
                "calc_vert_profiles": 0,
                "calc_rss_rbs": 0,
                "soil_heat_method": 2,
                "save_spectral": 1,
                "calc_xanthophyllabs": 0,
                "applTcorr": 0,
                "MoninObukhov" : 0,
                "lite": 0,
                
            }

            results_path = scope.run(multi_params, my_setoptions, save_parquet=True)

            results_df = pd.read_parquet(results_path)
            results = results_df.to_dict(orient="records")

            print("\n=== Results ===")

            print(
                f"Number of simulations in output: {results_df.shape[0]}"
            ) 

    except Exception as e:
        print(f"Error during SCOPE execution: {e}")


=== Path Diagnostics ===
Current working directory: /home/omirako/Documents/MSc_Sensors_Imaging/Final_Project
Checking for 'SCOPE' in: /home/omirako/Documents/MSc_Sensors_Imaging/Final_Project

=== Running Multi-Simulation Test ===
=== Parameters before CSV generation ===
{
  "Cab": [
    20.0,
    25,
    0,
    30.0,
    40.0,
    50.0
  ],
  "Cca": [
    10.0
  ],
  "Cdm": [
    0.012
  ],
  "Cw": [
    0.009
  ],
  "Cs": [
    0.0
  ],
  "Cant": [
    1.0
  ],
  "N": [
    1.5
  ],
  "Vcmax25": [
    60.0
  ],
  "BallBerrySlope": [
    8.0
  ],
  "BallBerry0": [
    0.01
  ],
  "LAI": [
    2.0,
    3.0,
    5.0,
    8.0,
    0.0
  ],
  "hc": [
    2.0
  ],
  "LIDFa": [
    -0.35
  ],
  "LIDFb": [
    -0.15
  ],
  "rss": [
    500.0
  ],
  "SMC": [
    25.0
  ],
  "Rin": [
    800.0
  ],
  "Ta": [
    20.0,
    30.0
  ],
  "Ca": [
    410.0
  ],
  "fqe": [
    0.01,
    0.03,
    0.06,
    0.1,
    0.2,
    0.5,
    1,
    2
  ],
  "tts": [
    35.0,
    0.0,
    60.0
  ],
  "tto"

In [5]:
results

[{'run_parameters': array([{'Aerodynamic.CD1': 20.6, 'Aerodynamic.CR': 0.35, 'Aerodynamic.CSSOIL': 0.01, 'Aerodynamic.Cd': 0.3, 'Aerodynamic.Psicor': 0.2, 'Aerodynamic.d': 1.34, 'Aerodynamic.rb': 10.0, 'Aerodynamic.rbs': 10.0, 'Aerodynamic.rwc': 0.0, 'Aerodynamic.zo': 0.25, 'Angles.psi': 0.0, 'Angles.tto': 0.0, 'Angles.tts': 35.0, 'Canopy.Cv': 1.0, 'Canopy.LAI': 2.0, 'Canopy.LIDFa': -0.35, 'Canopy.LIDFb': -0.15, 'Canopy.crowndiameter': 1.0, 'Canopy.hc': 2.0, 'Canopy.leafwidth': 0.1, 'Fluorescence.fqe': 0.01, 'Leaf_Biochemical.BallBerry0': 0.01, 'Leaf_Biochemical.BallBerrySlope': 8.0, 'Leaf_Biochemical.Kn0': 2.48, 'Leaf_Biochemical.Knalpha': 2.83, 'Leaf_Biochemical.Knbeta': 0.114, 'Leaf_Biochemical.Rdparam': 0.015, 'Leaf_Biochemical.Type': 0.0, 'Leaf_Biochemical.Vcmax25': 60.0, 'Leaf_Biochemical.kV': 0.64, 'Leaf_Biochemical_magnani.Tyear': 15.0, 'Leaf_Biochemical_magnani.beta': 0.51, 'Leaf_Biochemical_magnani.kNPQs': 0.0, 'Leaf_Biochemical_magnani.qLs': 1.0, 'Leaf_Biochemical_magnani.st

In [7]:
import pandas as pd

# Load the Parquet file
results_df = pd.read_parquet(results_path)

# Convert the DataFrame to a dictionary (assuming one row)
results_list = results_df.to_dict(orient="records")
if results_list:
    results = results_list[0]
    print("Top-level keys in results:")
    for key in results.keys():
        print(key)
    
    # Try accessing 'spectral_outputs' safely
    spectral_outputs = results.get("spectral_outputs")
    if spectral_outputs is None:
        print("Key 'spectral_outputs' not found in results. The structure might be flattened or named differently.")
    else:
        print("Keys in spectral_outputs:")
        for key in spectral_outputs.keys():
            print(key)
    
    # Similarly, check for 'input_parameters'
    input_parameters = results.get("input_parameters")
    if input_parameters is None:
        print("Key 'input_parameters' not found in results.")
    else:
        print("Keys in input_parameters:")
        for key in input_parameters.keys():
            print(key)
    
    # A recursive function to print keys in nested dictionaries/lists
    def print_keys(d, prefix=""):
        if isinstance(d, dict):
            for k, v in d.items():
                print(f"{prefix}{k}")
                if isinstance(v, dict):
                    print_keys(v, prefix=prefix + "-")
                elif isinstance(v, list) and v and isinstance(v[0], dict):
                    for item in v:
                        print_keys(item, prefix=prefix + "-")
        else:
            print(f"{prefix}{d}")

    print("Recursive key print:")
    print_keys(results)
else:
    print("No results found.")


Top-level keys in results:
run_parameters
num_simulations
wlF
wlS
input_parameters_PROSPECT_Cab
input_parameters_PROSPECT_Cca
input_parameters_PROSPECT_Cdm
input_parameters_PROSPECT_Cw
input_parameters_PROSPECT_Cs
input_parameters_PROSPECT_Cant
input_parameters_PROSPECT_Cp
input_parameters_PROSPECT_Cbc
input_parameters_PROSPECT_N
input_parameters_PROSPECT_rho_thermal
input_parameters_PROSPECT_tau_thermal
input_parameters_Leaf_Biochemical_Vcmax25
input_parameters_Leaf_Biochemical_BallBerrySlope
input_parameters_Leaf_Biochemical_BallBerry0
input_parameters_Leaf_Biochemical_Type
input_parameters_Leaf_Biochemical_kV
input_parameters_Leaf_Biochemical_Rdparam
input_parameters_Leaf_Biochemical_Kn0
input_parameters_Leaf_Biochemical_Knalpha
input_parameters_Leaf_Biochemical_Knbeta
input_parameters_Leaf_Biochemical_magnani_Tyear
input_parameters_Leaf_Biochemical_magnani_beta
input_parameters_Leaf_Biochemical_magnani_kNPQs
input_parameters_Leaf_Biochemical_magnani_qLs
input_parameters_Leaf_Bioche

In [9]:
import os
import logging
import shutil
import tempfile
import json
from pathlib import Path

import matlab.engine
import numpy as np
import pandas as pd
from scipy.interpolate import interp1d

# Path to your Parquet file
results_path = Path("synthetic_dataset/results.parquet")

# Load the Parquet file into a DataFrame
results_df = pd.read_parquet(results_path)

# Print out the columns so you can inspect the flattened structure
print("Columns in results_df:")
print(results_df.columns)

# If the structure was flattened with an underscore, 
# try to access the "spectral_outputs_Esun" column:
if "spectral_outputs_Esun" in results_df.columns:
    esun = results_df["spectral_outputs_Esun"].iloc[0]
    print("Esun:", esun)
else:
    print("Column 'spectral_outputs_Esun' not found in results_df.")

Columns in results_df:
Index(['run_parameters', 'num_simulations', 'wlF', 'wlS',
       'input_parameters_PROSPECT_Cab', 'input_parameters_PROSPECT_Cca',
       'input_parameters_PROSPECT_Cdm', 'input_parameters_PROSPECT_Cw',
       'input_parameters_PROSPECT_Cs', 'input_parameters_PROSPECT_Cant',
       'input_parameters_PROSPECT_Cp', 'input_parameters_PROSPECT_Cbc',
       'input_parameters_PROSPECT_N', 'input_parameters_PROSPECT_rho_thermal',
       'input_parameters_PROSPECT_tau_thermal',
       'input_parameters_Leaf_Biochemical_Vcmax25',
       'input_parameters_Leaf_Biochemical_BallBerrySlope',
       'input_parameters_Leaf_Biochemical_BallBerry0',
       'input_parameters_Leaf_Biochemical_Type',
       'input_parameters_Leaf_Biochemical_kV',
       'input_parameters_Leaf_Biochemical_Rdparam',
       'input_parameters_Leaf_Biochemical_Kn0',
       'input_parameters_Leaf_Biochemical_Knalpha',
       'input_parameters_Leaf_Biochemical_Knbeta',
       'input_parameters_Leaf_Biochem

In [17]:
import os
import logging
import shutil
import tempfile
import struct
import re
from collections import defaultdict
from pathlib import Path

import matlab.engine
import numpy as np
import pandas as pd
from scipy.interpolate import interp1d

# --- Configuration ---
BASE_DIR = Path("./")
MODTRAN_MATLAB_DIR = BASE_DIR / "MODTRAN5" / "matlab-modtran-5-aba70d781805"
# We now assume SCOPE results are saved in Parquet format:
RESULTS_PARQUET_FILE = BASE_DIR / "synthetic_dataset" / "results.parquet"
OUTPUT_DIR = BASE_DIR / "output"
OUTPUT_DIR.mkdir(parents=True, exist_ok=True)

# --- Logging Setup ---
logging.basicConfig(level=logging.INFO,
                    format="%(asctime)s [%(levelname)s] %(message)s",
                    handlers=[logging.StreamHandler()])
logger = logging.getLogger(__name__)

# --- MODTRAN Configuration ---
MODTRAN_DIR = Path("/home/omirako/Documents/MSc_Sensors_Imaging/Final_Project/MODTRAN5").resolve()
logger.info(f"Looking for MODTRAN at: {MODTRAN_DIR}")
if not MODTRAN_DIR.exists():
    raise FileNotFoundError(f"MODTRAN directory not found: {MODTRAN_DIR}")

MODTRAN_EXE_DIR = MODTRAN_DIR / "bin"
if not MODTRAN_EXE_DIR.exists():
    raise FileNotFoundError(f"MODTRAN executable directory not found: {MODTRAN_EXE_DIR}")

possible_data_dirs = [MODTRAN_EXE_DIR / "DATA", MODTRAN_DIR / "DATA", MODTRAN_DIR / "data"]
MODTRAN_DATA_DIR = next((d for d in possible_data_dirs if d.exists()), None)
if MODTRAN_DATA_DIR:
    logger.info(f"Found MODTRAN data directory at: {MODTRAN_DATA_DIR}")
else:
    raise FileNotFoundError(f"MODTRAN data directory not found. Searched in: {possible_data_dirs}")

possible_bmfiles = [MODTRAN_DATA_DIR / "p1_2013.bin", MODTRAN_DATA_DIR / "p1_2009t.bin",
                    MODTRAN_DATA_DIR / "p1_2009c.bin", MODTRAN_DATA_DIR / "p1_2009.bin"]
BMNAME_FILE = next((f for f in possible_bmfiles if f.exists()), None)
if BMNAME_FILE:
    logger.info(f"Found band model: {BMNAME_FILE.name}, but it will be ignored.")
else:
    logger.info("No band model file found. Proceeding with MODTRAN defaults.")

# --- Start MATLAB Engine ---
logger.info("Starting MATLAB Engine...")
eng = matlab.engine.start_matlab("-nojvm -nodisplay -nosplash")

# --- Configure MATLAB Paths ---
eng.addpath(str(MODTRAN_DIR.resolve()), nargout=0)
eng.addpath(eng.genpath(str(MODTRAN_MATLAB_DIR.resolve())), nargout=0)
eng.addpath(str(MODTRAN_DATA_DIR.resolve()), nargout=0)

import platform
os_type = platform.system()
if os_type == "Windows":
    modtran_exe = MODTRAN_EXE_DIR / "Mod5_win64.exe"
elif os_type == "Linux":
    modtran_exe = MODTRAN_EXE_DIR / "Mod5_linux.exe"
    if not modtran_exe.exists():
        modtran_exe = MODTRAN_EXE_DIR / "Mod5_linux.exe"

modtran_matlab_dir = MODTRAN_MATLAB_DIR.resolve()
modtran_exe_dir = MODTRAN_EXE_DIR.resolve()
modtran_exe_path = modtran_exe.resolve()
relative_modtran_path = os.path.relpath(str(modtran_exe_dir), str(modtran_matlab_dir))
relative_modtran_exe = os.path.relpath(str(modtran_exe_path), str(modtran_matlab_dir))

# --- Create temporary MATLAB function to override GUI dialog ---
temp_script = f"""
function [MODTRANExe, MODTRANPath] = SetMODTRANExe()
    MODTRANExe = '{modtran_exe.name}';
    MODTRANPath = '{str(MODTRAN_EXE_DIR.resolve()).replace(os.sep, '/')}/';
end
"""
temp_dir = Path(tempfile.mkdtemp())
script_path = temp_dir / "SetMODTRANExe.m"
with open(script_path, 'w') as f:
    f.write(temp_script)
eng.addpath(str(temp_dir), nargout=0)
eng.eval("Mod5.SetMODTRANExe = @SetMODTRANExe;", nargout=0)
eng.workspace["MODTRANPath"] = relative_modtran_path.replace(os.sep, '/') + "/"
eng.workspace["MODTRANExe"] = relative_modtran_exe.replace(os.sep, '/')

logger.info("Final MATLAB configuration complete.")
try:
    modtran_path = eng.workspace['MODTRANPath']
except Exception:
    modtran_path = "Not Set"
logger.info(f"MODTRANPath in MATLAB: {modtran_path}")
try:
    modtran_exe_ws = eng.workspace['MODTRANExe']
except Exception:
    modtran_exe_ws = "Not Set"
logger.info(f"MODTRANExe in MATLAB: {modtran_exe_ws}")
logger.info(f"Is Mod5.m found? {eng.exist('Mod5.m', 'file')}")
logger.info(f"Is run_MODTRAN5_AC_PAR_4RUNS.m found? {eng.exist('run_MODTRAN5_AC_PAR_4RUNS.m', 'file')}")

eng.addpath(str(MODTRAN_MATLAB_DIR.resolve()), nargout=0)
eng.addpath(eng.genpath(str((MODTRAN_MATLAB_DIR.parent / "modtran5_acd_t14").resolve())), nargout=0)
logger.info("MATLAB paths added successfully.")

# --- Helper Functions ---
def run_modtran_matlab(parms, output_dir, case_name):
    """Runs MODTRAN via MATLAB Engine with proper initialization."""
    try:
        eng.eval("warning('off', 'Mod5:setBMNAME:FileNotFound');", nargout=0)
        eng.workspace['NSTR'] = 1  # Force single-threaded execution
        eng.eval("delete(gcp('nocreate'));", nargout=0)
        matlab_parms = eng.struct()
        for key, value in parms.items():
            if key == 'ATM':
                atm_struct = eng.struct()
                for sub_key, sub_value in value.items():
                    if isinstance(sub_value, (list, np.ndarray)):
                        atm_struct[sub_key] = matlab.double([float(x) for x in sub_value])
                    elif isinstance(sub_value, (int, float)):
                        atm_struct[sub_key] = float(sub_value)
                    else:
                        atm_struct[sub_key] = sub_value
                matlab_parms[key] = atm_struct
            elif key == 'SPECTRAL':
                spectral_struct = eng.struct()
                for sub_key, sub_value in value.items():
                    if sub_key in ('V1', 'V2'):
                        spectral_struct[sub_key] = matlab.double([float(sub_value)])
                    elif isinstance(sub_value, (int, float)):
                        spectral_struct[sub_key] = float(sub_value)
                    else:
                        spectral_struct[sub_key] = sub_value
                matlab_parms[key] = spectral_struct
            else:
                if isinstance(value, (list, np.ndarray)):
                    matlab_parms[key] = matlab.double([float(x) for x in value])
                elif isinstance(value, (int, float)):
                    matlab_parms[key] = float(value)
                else:
                    matlab_parms[key] = value
        eng.cd(str(MODTRAN_MATLAB_DIR.resolve()), nargout=0)
        wvlLUT, T14, _ = eng.run_MODTRAN5_AC_PAR_4RUNS(
            str(output_dir),
            case_name,
            matlab_parms,
            'FLUO',
            'A',
            1,
            0,
            0,
            nargout=3
        )
        return np.array(wvlLUT), np.array(T14)
    except Exception as e:
        logger.error(f"MODTRAN execution failed for {case_name}: {e}")
        return None, None

def interpolate_and_combine(wl_scope, data_scope, wl_modtran):
    """Interpolates SCOPE data to MODTRAN wavelengths."""
    interpolator = interp1d(wl_scope, data_scope, kind='linear', bounds_error=False, fill_value="extrapolate")
    return interpolator(wl_modtran)

def validate_modtran_params(parms):
    required_atm = ['WVL', 'WNDFNM', 'WLINC', 'MODEL', 'H1', 'SZA', 'IHAZE', 'VIS']
    for param in required_atm:
        if param not in parms['ATM']:
            raise ValueError(f"Missing required ATM parameter: {param}")
    required_top_level = ['SPECTRAL', 'GEOM']
    for param in required_top_level:
        if param not in parms:
            raise ValueError(f"Missing required top-level parameter: {param}")
    numerical_params = {
        'ATM': ['AOT', 'H1', 'SZA', 'VZA', 'GNDALT', 'WLINC','VIS'],
        'SPECTRAL': ['V1', 'V2', 'DV', 'FWHM'],
        'GEOM': ['H1ALT', 'OBSZEN'],
        'top_level': ['SFWHM', 'CO2MX', 'RAINRT', 'GNDALT','PARM1','PARM2']
    }
    for category, params in numerical_params.items():
        for param in params:
            if category == 'ATM':
                value = parms['ATM'].get(param)
            elif category == 'SPECTRAL':
                value = parms['SPECTRAL'].get(param)
            elif category == 'GEOM':
                value = parms['GEOM'].get(param)
            else:
                value = parms.get(param)
            if value is None:
                raise ValueError(f"Parameter {param} is required but has no value assigned")
            if isinstance(value, (list, np.ndarray)):
                if not all(isinstance(x, (int, float)) for x in value):
                    raise TypeError(f"Elements of parameter {param} must be numeric")
            elif not isinstance(value, (int, float)):
                raise TypeError(f"Parameter {param} must be numeric, got {type(value)}")

def make_hashable(o):
    """Recursively convert a dict or list into a hashable type (tuple)."""
    if isinstance(o, dict):
        return tuple(sorted((k, make_hashable(v)) for k, v in o.items()))
    elif isinstance(o, list):
        return tuple(make_hashable(x) for x in o)
    else:
        return o

# --- Main Processing ---
if __name__ == "__main__":
    # Load SCOPE Results from Parquet.
    try:
        results_df = pd.read_parquet(RESULTS_PARQUET_FILE)
        # Assume one row; convert to dictionary.
        scope_results = results_df.iloc[0].to_dict()
    except Exception as e:
        logger.error(f"Error loading SCOPE results from Parquet: {e}")
        exit(1)

    # Save common lookup tables in Parquet (no JSON)
    global_lookup = {
        "SCOPE_wlS": np.array(scope_results.get("wlS", [])).tolist(),
        "SCOPE_wlF": np.array(scope_results.get("wlF", [])).tolist()
    }
    # If modtran_wavelength is present, add it; otherwise empty list.
    global_lookup["modtran_wavelength"] = np.array(scope_results.get("spectral_outputs_modtran_wavelength", [])).tolist()
    global_lookup_file = OUTPUT_DIR / "simulation_lookuptable.parquet"
    df_lookup = pd.DataFrame([global_lookup])
    df_lookup.to_parquet(global_lookup_file, index=False)
    logger.info(f"Saved global lookup table to {global_lookup_file}")

    num_simulations = scope_results.get('num_simulations', 0)
    logger.info(f"Number of SCOPE simulations: {num_simulations}")

    run_params = scope_results.get("run_parameters", [])
    input_parameters = scope_results.get("input_parameters", {})

    # Prepare SCOPE spectral data arrays.
    wlS = np.array(scope_results['wlS'])[0]  # assume a single list
    wlF = np.array(scope_results['wlF'])[0]
    # Flattened keys from json_normalize use underscores.
    reflectance_data = np.array(scope_results['spectral_outputs_reflectance'])
    fluorescence_data = np.array(scope_results['spectral_outputs_fluorescence'])

    modtran_cache = {}
    modtran_results = []
    global_lookup_saved = False

    for i in range(num_simulations):
        current_scope = run_params[i]
        base_shared = {
            "SZA": current_scope.get("Angles.tts", 30.0),
            "TPTEMP": current_scope.get("Meteo.Ta", 20.0),
            "CO2": current_scope.get("Meteo.Ca", 410.0),
            "psi": current_scope.get("Angles.psi", 0.0),
            "tto": current_scope.get("Angles.tto", 0.0),
        }
        
        # Default aerosol properties (baseline)
        default_aerosol = {
            "AOT": 0.1,       # Aerosol Optical Thickness
            "SSA": 0.95,      # Single Scattering Albedo
            "G": 0.7,         # Asymmetry factor
        }

        # Default cloud properties (clear-sky)
        default_cloud = {
            "cloud_fraction": 0.0,  # Fraction of sky covered by clouds (0 = clear)
            "cloud_optical_depth": 0,  # Optical depth of clouds (0 = none)
        }

        # Default water vapor (in cm)
        default_water = {
            "H2O": 2.0,       # Water vapor content
        }
        
        ambient_conditions = [
            # 1. Baseline: clear sky, typical pollutants
            dict(base_shared, O3=0.04, NO2=0.015, CO=0.2, **default_cloud, **default_aerosol, **default_water),
            # 2. Clear sky, slightly higher aerosol loading
            dict(base_shared, O3=0.04, NO2=0.015, CO=0.2, **default_cloud, AOT=0.12, **default_water),
            # 3. Clear sky, increased water vapor
            dict(base_shared, O3=0.04, NO2=0.015, CO=0.2, **default_cloud, **default_aerosol, H2O=2.5),
            # 4. Slight clouds, typical pollutants
            dict(base_shared, O3=0.04, NO2=0.015, CO=0.2, cloud_fraction=0.1, cloud_optical_depth=3, **default_aerosol, **default_water),
            # 5. Slight clouds, increased aerosol loading
            dict(base_shared, O3=0.04, NO2=0.015, CO=0.2, cloud_fraction=0.1, cloud_optical_depth=3, AOT=0.12, **default_water),
            # 6. Slight clouds, increased water vapor
            dict(base_shared, O3=0.04, NO2=0.015, CO=0.2, cloud_fraction=0.1, cloud_optical_depth=3, **default_aerosol, H2O=2.5),
            # 7. Moderate pollutants, clear sky
            dict(base_shared, O3=0.05, NO2=0.02, CO=0.3, **default_cloud, AOT=0.15, **default_water),
            # 8. Moderate pollutants, moderate clouds
            dict(base_shared, O3=0.05, NO2=0.02, CO=0.3, cloud_fraction=0.3, cloud_optical_depth=7, AOT=0.15, **default_water),
            # 9. Moderate pollutants, heavier clouds
            dict(base_shared, O3=0.05, NO2=0.02, CO=0.3, cloud_fraction=0.4, cloud_optical_depth=8, AOT=0.15, **default_water),
            # 10. Higher pollutants, clear sky
            dict(base_shared, O3=0.06, NO2=0.025, CO=0.4, **default_cloud, AOT=0.2, **default_water),
            # 11. Higher pollutants, moderate clouds
            dict(base_shared, O3=0.06, NO2=0.025, CO=0.4, cloud_fraction=0.5, cloud_optical_depth=10, AOT=0.2, **default_water),
            # 12. Higher pollutants, heavy clouds
            dict(base_shared, O3=0.06, NO2=0.025, CO=0.4, cloud_fraction=0.6, cloud_optical_depth=12, AOT=0.2, **default_water),
            # 13. Lower pollutants, clear sky
            dict(base_shared, O3=0.03, NO2=0.01, CO=0.1, **default_cloud, AOT=0.08, H2O=1.5),
            # 14. Lower pollutants, slight cloud cover
            dict(base_shared, O3=0.03, NO2=0.01, CO=0.1, cloud_fraction=0.2, cloud_optical_depth=4, AOT=0.08, H2O=1.5),
            # 15. Elevated NO₂, high CO, clear sky
            dict(base_shared, O3=0.045, NO2=0.03, CO=0.5, **default_cloud, AOT=0.18, **default_water),
            # 16. Elevated NO₂, high CO, moderate clouds
            dict(base_shared, O3=0.045, NO2=0.03, CO=0.5, cloud_fraction=0.3, cloud_optical_depth=9, AOT=0.18, **default_water),
            # 17. High CO, clear sky
            dict(base_shared, O3=0.05, NO2=0.015, CO=0.7, **default_cloud, AOT=0.16, **default_water),
            # 18. High CO, light clouds
            dict(base_shared, O3=0.05, NO2=0.015, CO=0.7, cloud_fraction=0.25, cloud_optical_depth=6, AOT=0.16, **default_water),
            # 19. Elevated NO₂ with moderately high CO, clear sky
            dict(base_shared, O3=0.04, NO2=0.03, CO=0.6, **default_cloud, AOT=0.19, **default_water),
            # 20. Elevated NO₂ with moderately high CO, moderate clouds
            dict(base_shared, O3=0.04, NO2=0.03, CO=0.6, cloud_fraction=0.35, cloud_optical_depth=10, AOT=0.19, **default_water),
        ]

        for j, ambient in enumerate(ambient_conditions):
            # Build the effective MODTRAN parameters dictionary (PARMS) using ambient conditions.
            # If a parameter is not provided in the ambient conditions dictionary, a default value is used.
            PARMS = {
                'CASE': ambient.get("CASE", 0),  # Simulation case identifier (default: 0)
                'MODTRN': ambient.get("MODTRN", 'M'),  # MODTRAN mode ('M' for standard mode)
                'SPEED': ambient.get("SPEED", 'S'),  # Simulation speed option (default: 'S')
                'LYMOLC': ambient.get("LYMOLC", 0),  # Molecule-specific option (default: 0)
                'MODEL': ambient.get("MODEL", 2),  # Atmospheric model selection (default: 2)
                'ITYPE': ambient.get("ITYPE", 3),  # Instrument/observation type (default: 3)
                'IEMSCT': ambient.get("IEMSCT", 3),  # Scattering option flag (default: 3)
                'IMULT': ambient.get("IMULT", 0),  # Multiplicative flag (default: 0)
                'M1': ambient.get("M1", 0),  # Additional model parameter M1 (default: 0)
                'M2': ambient.get("M2", 0),  # Additional model parameter M2 (default: 0)
                'M3': ambient.get("M3", 0),  # Additional model parameter M3 (default: 0)
                'M4': ambient.get("M4", 0),  # Additional model parameter M4 (default: 0)
                'M5': ambient.get("M5", 0),  # Additional model parameter M5 (default: 0)
                'M6': ambient.get("M6", 0),  # Additional model parameter M6 (default: 0)
                'MDEF': ambient.get("MDEF", 0),  # Model definition flag (default: 0)
                'I_RD2C': ambient.get("I_RD2C", 0),  # Radiative transfer option flag (default: 0)
                'NOPRNT': ambient.get("NOPRNT", 0),  # Print output flag (default: 0)
                'TPTEMP': ambient.get("TPTEMP", base_shared["TPTEMP"]),  # Temperature for Planck function (°C)
                'SURREF': ambient.get("SURREF", 'LAMB_1'),  # Surface reflection model (e.g., Lambertian)
                'DIS': ambient.get("DIS", '1'),  # Display/output option (default: '1')
                'DISAZM': ambient.get("DISAZM", '0'),  # Azimuth display flag (default: '0')
                'DISALB': ambient.get("DISALB", ' '),  # Albedo display placeholder
                'NSTR': ambient.get("NSTR", 8),  # Number of radiative transfer streams (default: 8)
                'SFWHM': ambient.get("SFWHM", 1.0),  # Instrument spectral response scaling factor (default: 1.0)
                'CO2MX': ambient.get("CO2", base_shared["CO2"]),  # CO₂ mixing ratio (ppm)
                'LSUNFL': ambient.get("LSUNFL", 1),  # Sun flag: include direct sun (default: 1)
                'LBMNAM': ambient.get("LBMNAM", 0),  # Disable band model lookup (default: 0)
                'BMNAME': ambient.get("BMNAME", ' '),  # Band model name (default: blank)
                'IDAY': ambient.get("IDAY", 191),  # Day of year for simulation (default: 191)
                'GMTIME': ambient.get("GMTIME", 12.0),  # Greenwich Mean Time (default: 12.0 hours)
                'NSSALB': ambient.get("NSSALB", 0),  # Spherical albedo placeholder
                'IPARM': ambient.get("IPARM", 11),  # Parameter flag (default: 11)
                'APLUS': ambient.get("APLUS", ' '),  # Additional parameter placeholder
                'CNOVAM': ambient.get("CNOVAM", ' '),  # Additional parameter placeholder
                'ARUSS': ambient.get("ARUSS", ' '),  # Additional parameter placeholder
                'SOLCON': ambient.get("SOLCON", ' '),  # Solar constant correction placeholder
                'LFLTNM': ambient.get("LFLTNM", ' '),  # Output filename placeholder
                'WSS': ambient.get("WSS", 0.0),  # Wind speed (default: 0.0)
                'WDS': ambient.get("WDS", 0.0),  # Wind direction (default: 0.0)
                'VIS': ambient.get("ATM_VIS", 23.0),  # Atmospheric visibility (km; default: 23.0)
                'RAINRT': ambient.get("RAINRT", 0.0),  # Rain rate (mm/hr; default: 0.0)
                'GNDALT': ambient.get("GNDALT", 1),  # Ground altitude (default: 1 km)
                'T_BEST': ambient.get("T_BEST", ' '),  # Best-fit temperature placeholder
                'ATM': {
                    'H1': ambient.get("H1", 1),  # Observer altitude (default: 1 km)
                    'GNDALT': ambient.get("GNDALT", 1),  # Ground altitude (default: 1 km)
                    'SZA': ambient.get("SZA", base_shared["SZA"]),  # Solar Zenith Angle (°)
                    'SAA': ambient.get("SAA", 180.0 - base_shared["psi"]),  # Solar Azimuth Angle (°)
                    'RAA': ambient.get("RAA", 0.0),  # Relative Azimuth Angle (°; default: 0)
                    'VZA': ambient.get("VZA", base_shared["tto"]),  # Observer Zenith Angle (°)
                    'MODEL': ambient.get("ATM_MODEL", 2),  # Atmospheric model selection (default: 2)
                    'IDAY': ambient.get("ATM_IDAY", 191),  # Day of year for ATM simulation (default: 191)
                    'G': ambient.get("G", 0.7),  # Asymmetry factor for scattering (default: 0.7)
                    'AOT': ambient.get("AOT", 0.1),  # Aerosol Optical Thickness (default: 0.1)
                    'CDASTM': ambient.get("CDASTM", ' '),  # Aerosol/storm parameters placeholder
                    'ASTMX': ambient.get("ASTMX", 0.0),  # Maximum aerosol optical thickness (default: 0.0)
                    'CMULT': ambient.get("CMULT", 1.0),  # Multiplicative factor for aerosol correction (default: 1.0)
                    'IHAZE': ambient.get("IHAZE", 1),  # Haze flag (default: 1)
                    'H2OSTR': ambient.get("H2O", 2.0),  # Water vapor content (default: 2.0)
                    'O3STR': str(ambient.get("O3", 'DEFAULT')),  # Ozone level (or 'DEFAULT' if not provided)
                    'C_PROF': ambient.get("C_PROF", ' '),  # Atmospheric profile placeholder
                    'H2OAER': ambient.get("H2OAER", ' '),  # Aerosol water content placeholder
                    'CDTDIR': ambient.get("CDTDIR", ' '),  # Direct irradiance component placeholder
                    'ASTMO': ambient.get("ASTMO", ' '),  # Additional aerosol options placeholder
                    'AERRH': ambient.get("AERRH", ' '),  # Aerosol error term placeholder
                    'IPH': ambient.get("IPH", 2),  # Photon counting flag (default: 2)
                    'ISEASN': ambient.get("ISEASN", 0),  # Additional aerosol parameter (default: 0)
                    'IVULCN': ambient.get("IVULCN", 0),  # Additional aerosol parameter (default: 0)
                    'ICSTL': ambient.get("ICSTL", 1),  # Cloud/scattering type flag (default: 1)
                    'ICLD': ambient.get("ICLD", 0),  # Cloudiness flag (default: 0)
                    'IVSA': ambient.get("IVSA", 0),  # Additional scattering parameter (default: 0)
                    'WVL': ambient.get("WVL", [650.0, 850.0]),  # Wavelength range (nm)
                    'WNDFNM': ambient.get("WNDFNM", [650.0, 850.0]),  # Lookup table wavelength range (nm)
                    'WLINC': ambient.get("WLINC", 1.0),  # Wavelength increment (nm)
                    'VIS': ambient.get("ATM_VIS", 23.0),  # Atmospheric visibility (km; default: 23.0)
                },
                'GEOM': {
                    'ITYPE': ambient.get("GEOM_ITYPE", 3),  # Geometric/observation type (default: 3)
                    'H1ALT': ambient.get("H1ALT", 500),  # Sensor altitude (m; default: 500)
                    'OBSZEN': ambient.get("OBSZEN", 180.0 - base_shared["tto"]),  # Observer Zenith Angle (°)
                    'TRUEAZ': ambient.get("TRUEAZ", base_shared["psi"] + 180.0),  # True azimuth angle (°)
                },
                'PARM1': ambient.get("PARM1", ambient.get("SZA", base_shared["SZA"])),  # Parameter 1 (default: SZA)
                'PARM2': ambient.get("PARM2", 0.0),  # Parameter 2 (default: 0.0)
                'SPECTRAL': {
                    'V1': ambient.get("V1", 1e7 / 850),  # Starting wavenumber (cm⁻¹, default from 850 nm)
                    'V2': ambient.get("V2", 1e7 / 650),  # Ending wavenumber (cm⁻¹, default from 650 nm)
                    'DV': ambient.get("DV", 20.0),  # Spectral resolution (cm⁻¹; lower DV gives higher resolution)
                    'FWHM': ambient.get("FWHM", 0.27),  # Instrument spectral response FWHM (default: 0.27)
                    'CM_1': ambient.get("CM_1", True),  # Flag indicating if the spectral range is in cm⁻¹ (True = yes)
                },
            }


            try:
                validate_modtran_params(PARMS)
            except Exception as e:
                logger.error(f"Validation failed for simulation sim_{i}_amb_{j}: {e}")
                continue

            modtran_key = make_hashable(PARMS)
            case_name = f"sim_{i}_amb_{j}"
            if modtran_key in modtran_cache:
                logger.info(f"Reusing cached MODTRAN simulation for {case_name}")
                wvlLUT, T14 = modtran_cache[modtran_key]
            else:
                logger.info(f"Running MODTRAN for {case_name}")
                wvlLUT, T14 = run_modtran_matlab(PARMS, str(OUTPUT_DIR), case_name)
                if wvlLUT is None:
                    logger.error(f"Skipping {case_name} due to MODTRAN error.")
                    continue
                modtran_cache[modtran_key] = (wvlLUT, T14)
                modtran_results.append({
                    "case_name": case_name,
                    "PARMS": PARMS,
                    "wavelength_modtran": wvlLUT.tolist()
                })

            wvlLUT = np.array(wvlLUT).flatten()
            idx_ref = i % reflectance_data.shape[0]
            # FIX: Since reflectance_data is 1D (each element is a reflectance array),
            # we index with a single index.
            R = interpolate_and_combine(wlS, reflectance_data[idx_ref], wvlLUT).flatten()
            F = interpolate_and_combine(wlF, fluorescence_data[idx_ref], wvlLUT).flatten()

            t_vals = {f't{j}': T14[:, j-1] for j in range(1, 13)}
            t1_val = t_vals['t1']
            t2_val = t_vals['t2']
            t3_val = t_vals['t3']
            t4_val = t_vals['t4'] + t_vals['t5']
            t6_val = t_vals['t6']
            t7_val = t_vals['t7']
            t8_val = t_vals['t8']
            t9_val = t_vals['t9']
            t10_val = t_vals['t10']
            t11_val = t_vals['t11']

            LBOA = t1_val * t4_val * R + t1_val * ((t9_val * R + t10_val * R + t11_val * R) / (1 - R * t3_val)) + t1_val * (t6_val * F + t7_val * F)
            LWLR = t1_val * t4_val + t1_val * ((t9_val * R + t10_val * R + t11_val * R) / (1 - R * t3_val))
            rho_app = LBOA / LWLR
            LTOA = t1_val * t2_val + (t1_val * t8_val * R + t9_val * R + t10_val * R + t11_val * R + t6_val * F + t7_val * F) / (1 - t3_val * R)
            print("wvlLUT shape:", wvlLUT.shape)
            print("LTOA shape:", LTOA.shape)
            
            if not global_lookup_saved:
                global_lookup = {
                    "SCOPE_wlS": np.array(wlS).tolist(),
                    "SCOPE_wlF": np.array(wlF).tolist(),
                    "modtran_wavelength": wvlLUT.tolist()
                }
                global_lookup_file = OUTPUT_DIR / "simulation_lookuptable.parquet"
                df_lookup = pd.DataFrame([global_lookup])
                df_lookup.to_parquet(global_lookup_file, index=False)
                logger.info(f"Saved global lookup table to {global_lookup_file}")
                global_lookup_saved = True

            sim_results = {
                "case_name": case_name,
                "SCOPE_settings": current_scope,
                "MODTRAN_settings": PARMS,
                "wavelength_modtran": wvlLUT.tolist(),
                "LTOA": LTOA.tolist(),
                "t_vals": {key: t_vals[key].tolist() for key in t_vals},
                "rho_app": rho_app.tolist(),
                "R": R.tolist(),
                "F": F.tolist(),
                "Esun": scope_results.get('spectral_outputs_Esun', [])[idx_ref],
                "lookup_table_reference": str(global_lookup_file)
            }

            output_file = OUTPUT_DIR / f"simulation_{case_name}.parquet"
            df_sim = pd.DataFrame([sim_results])
            df_sim.to_parquet(output_file, index=False)
            logger.info(f"Saved simulation results for {case_name} to {output_file}")

    eng.quit()
    shutil.rmtree(temp_dir)
    logger.info("MATLAB Engine quit and temporary files removed.")

    scope_results.setdefault("modtran_simulations", [])
    scope_results["modtran_simulations"].extend(modtran_results)
    df_overall = pd.json_normalize(scope_results, sep="_")
    parquet_path = RESULTS_PARQUET_FILE
    df_overall.to_parquet(parquet_path, index=False)
    logger.info(f"Final results saved in Parquet format at: {parquet_path}")

    logger.info("Processing complete.")


2025-03-23 02:56:40,186 [INFO] Looking for MODTRAN at: /home/omirako/Documents/MSc_Sensors_Imaging/Final_Project/MODTRAN5
2025-03-23 02:56:40,187 [INFO] Found MODTRAN data directory at: /home/omirako/Documents/MSc_Sensors_Imaging/Final_Project/MODTRAN5/bin/DATA
2025-03-23 02:56:40,188 [INFO] Found band model: p1_2009t.bin, but it will be ignored.
2025-03-23 02:56:40,188 [INFO] Starting MATLAB Engine...


2025-03-23 02:56:42,859 [INFO] Final MATLAB configuration complete.
2025-03-23 02:56:42,864 [INFO] MODTRANPath in MATLAB: ../bin/
2025-03-23 02:56:42,868 [INFO] MODTRANExe in MATLAB: ../bin/Mod5_linux.exe
2025-03-23 02:56:42,876 [INFO] Is Mod5.m found? 2.0
2025-03-23 02:56:42,885 [INFO] Is run_MODTRAN5_AC_PAR_4RUNS.m found? 2.0
2025-03-23 02:56:42,924 [INFO] MATLAB paths added successfully.
2025-03-23 02:56:43,003 [INFO] Saved global lookup table to output/simulation_lookuptable.parquet
2025-03-23 02:56:43,004 [INFO] Number of SCOPE simulations: 1440
2025-03-23 02:56:43,005 [INFO] Running MODTRAN for sim_0_amb_0


--- Starting run_MODTRAN5_AC_PAR_4RUNS at 23-Mar-2025 02:56:43 ---
MODTRAN5 - MIT 4 RUNS method (parallel version)
Initializing simulation parameters...
Cleared previous MODTRAN classes.
Atmospheric and geometric parameters set.
Loading tp5 base file for SENSOR: FLUO
TP5 base file loaded.
Base file parameters configured.
**************************************
MODTRAN5 is running in 1cm-1 configuration
**************************************
Output directory created at output/T14-Modtran
Initialized MODTRAN spectral output array.
Writing TP5 base file to: output/T14-Modtran/sim_0_amb_0.tp5
TP5 base file written.
Initializing MODTRAN5 cases...
MODTRAN5 cases initialized.
Loading MODTRANExe settings...
Using MODTRANPath: /home/omirako/Documents/MSc_Sensors_Imaging/Final_Project/MODTRAN5/bin/
Using MODTRANExe: /home/omirako/Documents/MSc_Sensors_Imaging/Final_Project/MODTRAN5/bin/Mod5_linux.exe
Starting parallel pool (parpool) using the 'local' profile ...
Connected to parallel pool with 4 

2025-03-23 02:57:00,435 [INFO] Saved global lookup table to output/simulation_lookuptable.parquet
2025-03-23 02:57:00,462 [INFO] Saved simulation results for sim_0_amb_0 to output/simulation_sim_0_amb_0.parquet
2025-03-23 02:57:00,463 [INFO] Running MODTRAN for sim_0_amb_1


Final output saved to output/T14fnct_sim_0_amb_0.mat
--- run_MODTRAN5_AC_PAR_4RUNS finished at 23-Mar-2025 02:57:00 ---
wvlLUT shape: (3620,)
LTOA shape: (3620,)
Parallel pool using the 'Processes' profile is shutting down.
--- Starting run_MODTRAN5_AC_PAR_4RUNS at 23-Mar-2025 02:57:02 ---
MODTRAN5 - MIT 4 RUNS method (parallel version)
Initializing simulation parameters...
Cleared previous MODTRAN classes.
Atmospheric and geometric parameters set.
Loading tp5 base file for SENSOR: FLUO
TP5 base file loaded.
Base file parameters configured.
**************************************
MODTRAN5 is running in 1cm-1 configuration
**************************************
Output directory created at output/T14-Modtran
Initialized MODTRAN spectral output array.
Writing TP5 base file to: output/T14-Modtran/sim_0_amb_1.tp5
TP5 base file written.
Initializing MODTRAN5 cases...
MODTRAN5 cases initialized.
Loading MODTRANExe settings...
Using MODTRANPath: /home/omirako/Documents/MSc_Sensors_Imaging/Final

...

2025-03-23 03:17:33,369 [INFO] Saved simulation results for sim_1438_amb_7 to output/simulation_sim_1438_amb_7.parquet
2025-03-23 03:17:33,370 [INFO] Reusing cached MODTRAN simulation for sim_1438_amb_8
2025-03-23 03:17:33,382 [INFO] Saved simulation results for sim_1438_amb_8 to output/simulation_sim_1438_amb_8.parquet
2025-03-23 03:17:33,382 [INFO] Reusing cached MODTRAN simulation for sim_1438_amb_9
2025-03-23 03:17:33,394 [INFO] Saved simulation results for sim_1438_amb_9 to output/simulation_sim_1438_amb_9.parquet
2025-03-23 03:17:33,394 [INFO] Reusing cached MODTRAN simulation for sim_1438_amb_10
2025-03-23 03:17:33,406 [INFO] Saved simulation results for sim_1438_amb_10 to output/simulation_sim_1438_amb_10.parquet
2025-03-23 03:17:33,407 [INFO] Reusing cached MODTRAN simulation for sim_1438_amb_11
2025-03-23 03:17:33,418 [INFO] Saved simulation results for sim_1438_amb_11 to output/simulation_sim_1438_amb_11.parquet
2025-03-23 03:17:33,419 [INFO] Reusing cached MODTRAN simulatio

wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)


2025-03-23 03:17:33,581 [INFO] Saved simulation results for sim_1439_amb_4 to output/simulation_sim_1439_amb_4.parquet
2025-03-23 03:17:33,582 [INFO] Reusing cached MODTRAN simulation for sim_1439_amb_5
2025-03-23 03:17:33,593 [INFO] Saved simulation results for sim_1439_amb_5 to output/simulation_sim_1439_amb_5.parquet
2025-03-23 03:17:33,594 [INFO] Reusing cached MODTRAN simulation for sim_1439_amb_6
2025-03-23 03:17:33,606 [INFO] Saved simulation results for sim_1439_amb_6 to output/simulation_sim_1439_amb_6.parquet
2025-03-23 03:17:33,606 [INFO] Reusing cached MODTRAN simulation for sim_1439_amb_7
2025-03-23 03:17:33,618 [INFO] Saved simulation results for sim_1439_amb_7 to output/simulation_sim_1439_amb_7.parquet
2025-03-23 03:17:33,618 [INFO] Reusing cached MODTRAN simulation for sim_1439_amb_8
2025-03-23 03:17:33,630 [INFO] Saved simulation results for sim_1439_amb_8 to output/simulation_sim_1439_amb_8.parquet
2025-03-23 03:17:33,630 [INFO] Reusing cached MODTRAN simulation for 

wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)
wvlLUT shape: (3620,)
LTOA shape: (3620,)


2025-03-23 03:17:34,051 [INFO] Final results saved in Parquet format at: synthetic_dataset/results.parquet
2025-03-23 03:17:34,051 [INFO] Processing complete.
